In [1]:
import os, sys, copy, sumolib, json, datetime
import pandas as pd
import numpy as np

In [2]:
class DailyPreprocessor():
    def __init__(self):
        pass
self = DailyPreprocessor()

In [3]:
# 루트폴더 지정
self.path_root = os.path.dirname(os.path.dirname(os.path.join(os.path.abspath('.'))))
print(self.path_root)

with open(os.path.join(self.path_root, 'configs', 'config.json'), 'r') as file:
    config = json.load(file)

# 주요 폴더 경로 지정
self.paths = config['paths']
self.path_data = os.path.join(self.path_root, *self.paths['data'])
self.path_intermediates = os.path.join(self.path_root, *self.paths['intermediates'])
self.path_results = os.path.join(self.path_root, *self.paths['results'])
self.path_tables = os.path.join(self.path_root, *self.paths['tables'])
self.path_networks = os.path.join(self.path_root, *self.paths['networks'])
self.path_scripts = os.path.join(self.path_root, *self.paths['scripts'])
print(self.path_data)
print(self.path_intermediates)
print(self.path_results)
print(self.path_tables)
print(self.path_networks)
print(self.path_scripts)

c:\Github\snits_siggen
c:\Github\snits_siggen\Data
c:\Github\snits_siggen\Intermediates
c:\Github\snits_siggen\Results
c:\Github\snits_siggen\Data\tables
c:\Github\snits_siggen\Data\networks
c:\Github\snits_siggen\Scripts


In [4]:
# 1-1. 네트워크 불러오기
self.net = sumolib.net.readNet(os.path.join(self.path_networks, 'sn.net.xml'))

In [5]:
# 1-2. 테이블 불러오기
# csv_files = [filename for filename in os.listdir(self.path_tables) if filename.endswith('csv')]
# COLUMNS = []
# for csv_file in csv_files:
#     df = pd.read_csv(os.path.join(self.path_tables, csv_file))
#     columns = list(df.columns)
#     COLUMNS.extend(columns)
# COLUMNS = sorted(set(COLUMNS))
self.alphs = ['A', 'B']

loading_dtype_1 = {'CRSRD_ID':int,          'CRSRD_NM':str,          'CRSRD_TYPE':int,        
                   'CTRLER_TYPE':str,       'CYCL':int,              'DAY':int,               
                   'FLOW_NO':int,           'FRI_PLAN_NO':int,       'FRST_REG_DT':str,       
                   'GRP_NO':int,            'HOUR':int,              'LAST_MDFCN_DT':str,     
                   'LGTD':float,            'LOS_YN':int,            'LTTD':float,            
                   'MAIN_CRSRD_ID':str,     'MAIN_PHASE':int,        'MIN':int,               
                   'MNTH':int,              'MON_PLAN_NO':int,       'NODE_ID':str,           
                   'OFFSET':int,            'PHASE':int,             'PHASE_DT':str,          
                   'PLAN_NO':int,           'PPC_TYPE':int,          'RING':str,              
                   'RINGA_FLOW':int,        'RINGA_MIN_SEC':int,     'RINGA_RED_SEC':int,     
                   'RINGA_YELLO_SEC':int,   'RINGB_FLOW':int,        'RINGB_MIN_SEC':int,     
                   'RINGB_RED_SEC':int,     'RINGB_YELLO_SEC':int,   'SAT_PLAN_NO':int,       
                   'SIGL_ANGLE':str,        'STOS_NO':int,           'SUN_PLAN_NO':int,       
                   'THU_PLAN_NO':int,       'TRFLIG_TYPE':int,       'TUE_PLAN_NO':int,       
                   'USE_YN':int,            'WED_PLAN_NO':int,       'adj_inc_edge_id':str,   
                   'adj_out_edge_id':str,   'child_id':str,          'condition':str,         
                   'inc_edge_id':str,       'inter_no':int,          'inter_type':int,        
                   'node_id':str,           'out_edge_id':str,       'parent_id':str,         
                   'phase_no':int,          'ring_type':str,         'turn_type':str}
loading_dtype_2 = {f'RING{alph}_PHASE{i}':int for alph in self.alphs for i in range(1,9)}
loading_dtype = {**loading_dtype_1, **loading_dtype_2}

# 테이블 불러오기

# 수작업으로 만든 테이블
self.inter_node = pd.read_csv(os.path.join(self.path_tables, 'inter_node.csv'), dtype=loading_dtype)
self.turn_type  = pd.read_csv(os.path.join(self.path_tables, 'turn_type.csv'), dtype=loading_dtype)
self.uturn      = pd.read_csv(os.path.join(self.path_tables, 'uturn.csv'), dtype=loading_dtype)
self.u_condition= pd.read_csv(os.path.join(self.path_tables, 'u_condition.csv'), dtype=loading_dtype)
self.coord      = pd.read_csv(os.path.join(self.path_tables, 'coord.csv'), dtype=loading_dtype)
self.turn_type  = pd.read_csv(os.path.join(self.path_tables, 'turn_type.csv'), dtype=loading_dtype)

# DB에서 fetch하는 테이블
self.dayplan    = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_DAY_PLAN.csv'), dtype=loading_dtype)
self.holyplan   = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_HOLIDAY_PLAN.csv'), dtype=loading_dtype)
self.red_yel    = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_RED_YELLO.csv'), dtype=loading_dtype)
self.weekplan   = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_WEEK_PLAN.csv'), dtype=loading_dtype)
self.history    = pd.read_csv(os.path.join(self.path_tables, 'TL_IF_SIGL_CYCL.csv'), dtype=loading_dtype)
self.inter_info = pd.read_csv(os.path.join(self.path_tables, 'TM_FA_CRSRD.csv'), dtype=loading_dtype)
self.angle      = pd.read_csv(os.path.join(self.path_tables, 'TN_IF_SIGL_FLOW.csv'), dtype=loading_dtype)

# 컬럼명 변경
rename_cname_1 = {'CRSRD_ID':'inter_no',      'CRSRD_NM':'inter_name',    'CRSRD_TYPE':'inter_type',  
                  'CYCL':'cycle',             'DAY':'DD',                 'FLOW_NO':'move_no',        
                  'GRP_NO':'group_no',        'HOUR':'hh',                'LGTD':'inter_lon',         
                  'LTTD':'inter_lat',         'MAIN_CRSRD_ID':'parent_id','MAIN_PHASE':'main_phase',  
                  'MIN':'mm',                 'MNTH':'MM',                'NODE_ID':'node_id',        
                  'OFFSET':'offset',          'PHASE':'phase_no',         'RING':'ring_type',         
                  'RINGA_RED_SEC':'red_A',    'RINGA_YELLO_SEC':'yel_A',  'RINGB_RED_SEC':'red_B',    
                  'RINGB_YELLO_SEC':'yel_B',  'SIGL_ANGLE':'angle_code',  'PLAN_NO':'plan_no'}

rename_cname_2 = {f'RING{alph}_PHASE{i}':f'dura_{alph}{i}' for alph in self.alphs for i in range(1,9)}
rename_cname = {**rename_cname_1, **rename_cname_2}

self.dayplan    = self.dayplan.rename(columns=rename_cname)
self.holyplan   = self.holyplan.rename(columns=rename_cname)
self.red_yel    = self.red_yel.rename(columns=rename_cname)
self.weekplan   = self.weekplan.rename(columns=rename_cname)
self.history    = self.history.rename(columns=rename_cname)
self.inter_info = self.inter_info.rename(columns=rename_cname)
self.angle      = self.angle.rename(columns=rename_cname)

# 교차로목록, 노드목록 정의
self.inter_nos = [int(x) for x in sorted(self.inter_info.inter_no.unique())]
self.node_ids = sorted(self.inter_node.node_id.unique())

In [6]:
# 1-3. 네트워크 무결성 검사
# (생략)

In [7]:
# 1-4. 테이블 무결성 검사
# (생략)

In [8]:
self.inter_node

inter_no node_id  inter_type
0        175      i0           0
1        175     u00           1
2        176      i1           0
3        177      i2           0
4        177     u20           1
5        178      i3           0
6        178     u30           1
7        178     u31           1
8        178     u32           1
9        201      i8           0
10       202      i9           0
11       206      i7           0
12       210      i6           0
13       210     u60           1
14       178     c30           1

In [9]:
# 1-5. 주요 객체 (리스트, 딕셔너리) 저장

# 주교차로 / 부교차로 / 유턴교차로 / 연등교차로 노드id
self.parent_ids = sorted(self.inter_node[self.inter_node.inter_type==0].node_id.unique())
self.child_ids = sorted(self.inter_node[self.inter_node.inter_type==1].node_id.unique())
self.uturn_ids = sorted(self.uturn.node_id.unique())
self.coord_ids = sorted(self.coord.node_id.unique())

print(self.inter_nos)
print(self.node_ids )
print(self.parent_ids)
print(self.child_ids )
print(self.uturn_ids )
print(self.coord_ids )

[175, 176, 177, 178, 201, 202, 206, 210]
['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']
['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']
['c30', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']
['u00', 'u20', 'u30', 'u31', 'u32', 'u60']
['c30']


In [10]:
# 교차로번호 - 노드id 간 딕셔너리
self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))
self.inter2nodes = {inter:[key for key, value in self.node2inter.items() if value == inter] for inter in self.node2inter.values()}
self.inter2node = dict(zip(self.inter_node[self.inter_node.inter_type==0]['inter_no'], self.inter_node[self.inter_node.inter_type==0]['node_id']))
self.node2type = dict(zip(self.inter_node['node_id'], self.inter_node['inter_type']))
# 주교차로id - 부교차로id 간 딕셔너리
self.child2parent = dict()
for child_id in list(self.inter_node[self.inter_node.inter_type==1]['node_id'].unique()):
    inter_no = self.inter_node[self.inter_node.node_id==child_id].iloc[0].inter_no
    parent_id = self.inter_node[self.inter_node.inter_no==inter_no][self.inter_node[self.inter_node.inter_no==inter_no].inter_type==0].iloc[0].node_id
    self.child2parent[child_id] = parent_id
self.parent2childs = {parent_id:[key for key, value in self.child2parent.items() if value == parent_id] for parent_id in self.child2parent.values()}
print(self.node2inter)
print(self.inter2nodes)
print(self.inter2node)
print(self.node2type)
print(self.child2parent)
print(self.parent2childs)

{'i0': 175, 'u00': 175, 'i1': 176, 'i2': 177, 'u20': 177, 'i3': 178, 'u30': 178, 'u31': 178, 'u32': 178, 'i8': 201, 'i9': 202, 'i7': 206, 'i6': 210, 'u60': 210, 'c30': 178}
{175: ['i0', 'u00'], 176: ['i1'], 177: ['i2', 'u20'], 178: ['i3', 'u30', 'u31', 'u32', 'c30'], 201: ['i8'], 202: ['i9'], 206: ['i7'], 210: ['i6', 'u60']}
{175: 'i0', 176: 'i1', 177: 'i2', 178: 'i3', 201: 'i8', 202: 'i9', 206: 'i7', 210: 'i6'}
{'i0': 0, 'u00': 1, 'i1': 0, 'i2': 0, 'u20': 1, 'i3': 0, 'u30': 1, 'u31': 1, 'u32': 1, 'i8': 0, 'i9': 0, 'i7': 0, 'i6': 0, 'u60': 1, 'c30': 1}
{'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'u60': 'i6', 'c30': 'i3'}
{'i0': ['u00'], 'i2': ['u20'], 'i3': ['u30', 'u31', 'u32', 'c30'], 'i6': ['u60']}


In [11]:
# 1-6. 신호계획 테이블 통합

now = datetime.datetime.now()
# 월, 일
MM, DD, hh, mm = now.month, now.day, now.hour, now.minute
hplan = self.holyplan[(self.holyplan.MM==MM) & (self.holyplan.DD==DD)]

# 요일
dow_number = now.weekday()
dows = [dow for dow in self.weekplan.columns if dow.endswith('PLAN_NO')]
dows = dows[1:] + dows[0:1]
dow = dows[dow_number]

# (inter_no, plan_no) 목록 
if len(hplan):
    inter_pnos = list(zip(hplan['inter_no'], hplan['plan_no']))
else:
    inter_pnos = list(zip(self.weekplan.inter_no, self.weekplan[dow]))
# 통합된 테이블
self.plan = self.dayplan.copy()
self.plan['inter_pno'] = list(zip(self.plan['inter_no'], self.plan['plan_no']))
self.plan = self.plan[(self.plan.inter_pno.isin(inter_pnos))]
self.plan = self.plan.drop(columns='inter_pno')
self.plan.head()

inter_no  plan_no  hh  mm  cycle  offset  dura_A1  dura_A2  dura_A3  \
0       175        1   0   0    160      57       37       39       55   
1       175        1   7   0    170      40       40       42       55   
2       175        1   9   0    180      28       43       45       55   
3       175        1  18  30    190      18       46       48       55   
4       176        1   0   0    150     131       37       73       40   

   dura_A4  ...  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  dura_B5  \
0       29  ...        0       37       39       25       59        0   
1       33  ...        0       40       42       29       59        0   
2       37  ...        0       43       45       33       59        0   
3       41  ...        0       46       48       37       59        0   
4        0  ...        0       37       73       40        0        0   

   dura_B6  dura_B7  dura_B8               LAST_MDFCN_DT  
0        0        0        0  2024-07-12 16:36:43.702267  
1        0        0        0  2024-07-12 16:36:43.702267  
2        0        0        0  2024-07-12 16:36:43.702267  
3        0        0        0  2024-07-12 16:36:43.702267  
4        0        0        0  2024-07-12 16:36:43.702267  

[5 rows x 23 columns]

In [12]:
self.plan = self.dayplan.copy()
self.plan['inter_pno'] = list(zip(self.plan['inter_no'], self.plan['plan_no']))
self.plan = self.plan[(self.plan.inter_pno.isin(inter_pnos))]
self.plan = self.plan.drop(columns='inter_pno')
self.plan.head()

inter_no  plan_no  hh  mm  cycle  offset  dura_A1  dura_A2  dura_A3  \
0       175        1   0   0    160      57       37       39       55   
1       175        1   7   0    170      40       40       42       55   
2       175        1   9   0    180      28       43       45       55   
3       175        1  18  30    190      18       46       48       55   
4       176        1   0   0    150     131       37       73       40   

   dura_A4  ...  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  dura_B5  \
0       29  ...        0       37       39       25       59        0   
1       33  ...        0       40       42       29       59        0   
2       37  ...        0       43       45       33       59        0   
3       41  ...        0       46       48       37       59        0   
4        0  ...        0       37       73       40        0        0   

   dura_B6  dura_B7  dura_B8               LAST_MDFCN_DT  
0        0        0        0  2024-07-12 16:36:43.702267  
1        0        0        0  2024-07-12 16:36:43.702267  
2        0        0        0  2024-07-12 16:36:43.702267  
3        0        0        0  2024-07-12 16:36:43.702267  
4        0        0        0  2024-07-12 16:36:43.702267  

[5 rows x 23 columns]

In [13]:
df_attributes = [attr for attr in dir(self) if isinstance(getattr(self, attr), pd.DataFrame)]
df_attributes

['angle',
 'coord',
 'dayplan',
 'history',
 'holyplan',
 'inter_info',
 'inter_node',
 'plan',
 'red_yel',
 'turn_type',
 'u_condition',
 'uturn',
 'weekplan']

In [14]:
self.inter2node

{175: 'i0',
 176: 'i1',
 177: 'i2',
 178: 'i3',
 201: 'i8',
 202: 'i9',
 206: 'i7',
 210: 'i6'}

In [15]:
self.angle[:30]

inter_no  phase_no ring_type  move_no  STOS_NO angle_code
0        175         1         A       -1        0     179004
1        175         1         B       -1        0     003176
2        175         2         A       -1        0     001095
3        175         2         B       -1        0     179271
4        175         3         A       -1        0     092270
5        175         3         B       -1        0     090180
6        175         4         A       -1        0     268358
7        175         4         B       -1        0     270090
8        175         5         A       -1        0        NaN
9        175         5         B       -1        0        NaN
10       175         6         A       -1        0        NaN
11       175         6         B       -1        0        NaN
12       175         7         A       -1        0        NaN
13       175         7         B       -1        0        NaN
14       175         8         A       -1        0        NaN
15       175         8         B       -1        0        NaN
16       176         1         A       -1        0     180000
17       176         1         B       -1        0     359180
18       176         2         A       -1        0     180000
19       176         2         B       -1        0     180270
20       176         3         A       -1        0     270356
21       176         3         B       -1        0        NaN
22       176         4         A       -1        0        NaN
23       176         4         B       -1        0        NaN
24       176         5         A       -1        0        NaN
25       176         5         B       -1        0        NaN
26       176         6         A       -1        0        NaN
27       176         6         B       -1        0        NaN
28       176         7         A       -1        0        NaN
29       176         7         B       -1        0        NaN

In [16]:
self.angle_new = []
for inter_no in self.inter_nos:
    ang = self.angle[self.angle.inter_no==inter_no]
    max_phase_no = ang.dropna(subset='angle_code')['phase_no'].max()
    self.angle_new.append(ang[ang.phase_no <= max_phase_no])
self.angle = pd.concat(self.angle_new)

In [17]:
import matplotlib.pyplot as plt
self.angle = self.angle.copy()

self.angle['node_id'] = self.angle['inter_no'].map(self.inter2node)
self.angle['parent_id'] = self.angle['node_id']
self.angle = self.angle.drop(columns='move_no')
for index, row in self.angle.iterrows():
    node_id = row.node_id
    if not isinstance(row.angle_code, str) or len(row.angle_code)!=6:
        continue
    # 방위각
    inc_angle = int(row.angle_code[:3])
    out_angle = int(row.angle_code[3:])
    self.angle.at[index, 'inc_angle'] = inc_angle
    self.angle.at[index, 'out_angle'] = out_angle
    # 일반각 및 라디안으로 변환, 실제 방향 설정
    inc_angle = (90 - inc_angle) % 360
    inc_angle = inc_angle * np.pi / 180
    inc_vec_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
    out_angle = (90 - out_angle) % 360
    out_angle = out_angle * np.pi / 180
    out_vec_true = np.array([np.cos(out_angle), np.sin(out_angle)])

    # 진입로 목록
    inc_edge_ids = [edge.getID() for edge in self.net.getNode(node_id).getIncoming()]
    inc_vecs = []
    for inc_edge_id in inc_edge_ids:
        init_pt = self.net.getEdge(inc_edge_id).getShape()[-1]
        term_pt = self.net.getEdge(inc_edge_id).getShape()[-2]
        assert init_pt != term_pt
        inc_vec = np.array(term_pt) - np.array(init_pt)
        inc_vec = inc_vec / np.linalg.norm(inc_vec)
        inc_vecs.append(inc_vec)
    # 각도에 맞는 진입로 지정
    max_index = np.argmax([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs])
    inc_edge_id = inc_edge_ids[max_index]
    self.angle.at[index, 'inc_edge_id'] = inc_edge_id

    # 진출로 목록
    out_edge_ids = [edge.getID() for edge in self.net.getNode(node_id).getOutgoing()]
    out_vecs = []
    for out_edge_id in out_edge_ids:
        init_pt = self.net.getEdge(out_edge_id).getShape()[0]
        term_pt = self.net.getEdge(out_edge_id).getShape()[1]
        assert init_pt != term_pt
        out_vec = np.array(term_pt) - np.array(init_pt)
        out_vec = out_vec / np.linalg.norm(out_vec)
        out_vecs.append(out_vec)
    # 각도에 맞는 진출로 지정
    max_index = np.argmax([np.dot(out_vec, out_vec_true) for out_vec in out_vecs])
    out_edge_id = out_edge_ids[max_index]
    self.angle.at[index, 'out_edge_id'] = out_edge_id
self.angle = self.angle.drop(columns='angle_code')

In [18]:
# turn_type 지정
io2turn_type = dict()
for row in self.turn_type.itertuples():
    if not (row.inc_edge_id, row.out_edge_id) in io2turn_type:
        io2turn_type[(row.inc_edge_id, row.out_edge_id)] = row.turn_type
    else:
        if io2turn_type[(row.inc_edge_id, row.out_edge_id)] != row.turn_type:
            print('the dictionary is not well-defined')
self.angle['turn_type'] = self.angle.apply(lambda row:io2turn_type.get((row['inc_edge_id'], row['out_edge_id']), None), axis=1)
self.angle['turn_type'] = self.angle['turn_type'].map({'straight': 'S', 'left': 'L', 'right': 'R'})
# node_type 지정
self.angle['node_type'] = 'normal'

In [19]:
u_condition = dict(zip(self.u_condition.child_id, self.u_condition.condition))
self.u_condition
u_condition

{'u00': '좌회전시',
 'u20': '보행신호시',
 'u30': '보행신호시',
 'u31': '보행신호시',
 'u32': '보행신호시',
 'u60': '좌회전시'}

In [20]:
self.angle_sep = 20

ne2angle = dict() # (node_id, edge_id) -> angle
NIA = [] # (node_id, inc_edge_id, angle)
NIs = set(zip(self.angle.node_id, self.angle.inc_edge_id)) # (node_id, inc_edge_id)
NIs = sorted(ni for ni in NIs if not pd.isna(ni[1]))
for node_id, inc_edge_id in NIs:
    ang = self.angle[(self.angle.node_id==node_id) & (self.angle.inc_edge_id==inc_edge_id)]
    mean_x = np.mean(np.cos(np.deg2rad(ang.inc_angle)))
    mean_y = np.mean(np.sin(np.deg2rad(ang.inc_angle)))
    mean_angle = int(np.rad2deg(np.arctan2(mean_y, mean_x)) % 360)
    NIA.append(pd.DataFrame({'node_id':[node_id], 'inc_edge_id':[inc_edge_id], 'angle':[mean_angle]}))
NIA = pd.concat(NIA).reset_index(drop=True)
NOA = [] # (node_id, out_edge_id, angle)
NOs = set(zip(self.angle.node_id, self.angle.out_edge_id)) # (node_id, out_edge_id)
NOs = sorted(no for no in NOs if not pd.isna(no[1]))
for node_id, out_edge_id in NOs:
    ang = self.angle[(self.angle.node_id==node_id) & (self.angle.out_edge_id==out_edge_id)]
    mean_x = np.mean(np.cos(np.deg2rad(ang.out_angle)))
    mean_y = np.mean(np.sin(np.deg2rad(ang.out_angle)))
    mean_angle = int(np.rad2deg(np.arctan2(mean_y, mean_x)) % 360)
    NOA.append(pd.DataFrame({'node_id':[node_id], 'out_edge_id':[out_edge_id], 'angle':[mean_angle]}))
NOA = pd.concat(NOA).reset_index(drop=True)

In [21]:
uangles = []
for uturn_id in self.uturn_ids:
    parent_id = self.child2parent[uturn_id] # 주교차로 노드id
    condition = u_condition[uturn_id] # 유턴조건
    # 바꿔서 넣을 데이터프레임
    uangle = self.angle[self.angle.parent_id==parent_id].copy() # 'angle' dataframe for a specific 'parent_id'
    uangle['node_id'] = uturn_id
    uangle['node_type'] = 'uturn'
    # 유턴에 관한 정보
    urow = self.uturn[self.uturn.node_id==uturn_id].iloc[0]
    node_id = urow.parent_id
    inc_edge_id = urow.inc_edge_id # 유턴 진입엣지id
    out_edge_id = urow.out_edge_id # 유턴 진출엣지id
    adj_inc_edge_id = urow.adj_inc_edge_id # 유턴 인접진입엣지id
    adj_out_edge_id = urow.adj_out_edge_id # 유턴 인접진출엣지id

    # 해당 노드에 대한 (노드id, 진입(출)엣지id, 방위각) 데이터프레임
    nia = NIA[NIA.node_id==node_id].sort_values(by='angle').reset_index(drop=True)
    noa = NOA[NOA.node_id==node_id].sort_values(by='angle').reset_index(drop=True)

    # 진입엣지 각도
    inc_angle = nia[nia.inc_edge_id==adj_inc_edge_id].iloc[0].angle

    # 진/출입로 각도 목록 (extended)
    inc_angles = np.array(nia.angle)
    inc_angles = np.concatenate((inc_angles - 360, inc_angles, inc_angles + 360))
    out_angles = np.array(noa.angle)
    out_angles = np.concatenate((out_angles - 360, out_angles, out_angles + 360))

    # 좌측 진출로 (좌회전신호시 진출로)
    out_angles_left = out_angles[out_angles >= inc_angle + self.angle_sep]
    out_angle_left = np.sort(out_angles_left)[0] % 360
    out_edge_id_left = noa[noa.angle==out_angle_left].iloc[0].out_edge_id

    # 좌측 진입로 (보행신호시 진입로)
    inc_angles_left = inc_angles[inc_angles >= inc_angle + self.angle_sep]
    inc_angle_left = np.sort(inc_angles_left)[0] % 360
    inc_edge_id_left = nia[nia.angle==inc_angle_left].iloc[0].inc_edge_id

    # 우측 진출로 (보행신호시 진출로)
    out_angles_right = out_angles[out_angles <= inc_angle - self.angle_sep]
    out_angle_right = np.sort(out_angles_right)[-1] % 360
    out_edge_id_right = noa[noa.angle==out_angle_right].iloc[0].out_edge_id

    # 좌회전시 조건
    left_flag = (uangle.inc_edge_id==adj_inc_edge_id) & (uangle.out_edge_id==out_edge_id_left) & (uangle.turn_type=='L')

    # 보행신호시 조건
    pedes_flag = (uangle.inc_edge_id==inc_edge_id_left) & (uangle.out_edge_id==out_edge_id_right)

    # 진출엣지가 유턴 인접진출엣지와 다르다는 조건
    out_adj_coincides = uangle[uangle.out_edge_id==adj_out_edge_id]
    out_adj_flag = ~uangle.phase_no.isin(out_adj_coincides.phase_no)

    if condition == '좌회전시':
        # 유턴교차로에 대한 from / to 재입력
        uangle.loc[left_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        uangle.loc[~left_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']

    elif condition == '보행신호시':
        # 유턴교차로에 대한 from / to 재입력
        uangle.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        uangle.loc[~pedes_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']

    uturn_not_assigned = (uangle[['inc_edge_id', 'out_edge_id']] == ('', '')).any(axis=1).all()
    if uturn_not_assigned:
        if left_flag.any():
            uangle.loc[left_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
            uangle.loc[~left_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']
        elif pedes_flag.any():
            uangle.loc[left_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
            uangle.loc[~left_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']
        elif out_adj_flag.any():
            uangle.loc[out_adj_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
            uangle.loc[~out_adj_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']
    uangles.append(uangle)

In [22]:
uangle

inter_no  phase_no ring_type  STOS_NO node_id parent_id  inc_angle  \
112       210         1         A        0     u60        i6       90.0   
113       210         1         B        0     u60        i6        NaN   
114       210         2         A        0     u60        i6      268.0   
115       210         2         B        0     u60        i6      270.0   
116       210         3         A        0     u60        i6      359.0   
117       210         3         B        0     u60        i6        0.0   
118       210         4         A        0     u60        i6      180.0   
119       210         4         B        0     u60        i6      180.0   

     out_angle   inc_edge_id    out_edge_id turn_type node_type  
112      270.0                                      S     uturn  
113        NaN                                    NaN     uturn  
114        0.0  571500535_02  -571500535_02         L     uturn  
115       90.0                                      S     uturn  
116       90.0                                      L     uturn  
117      180.0                                      S     uturn  
118        0.0                                      S     uturn  
119      270.0                                      L     uturn

In [23]:
# 연등교차로 처리
self.coord[['inc_edge_id', 'out_edge_id']] = self.coord[['inc_edge_id', 'out_edge_id']].fillna('')
self.coord['node_type'] = 'coord'
self.coord

inter_no parent_id node_id  STOS_NO  phase_no ring_type      inc_edge_id  \
0       178        i3     c30        0         1         A                    
1       178        i3     c30        0         1         B                    
2       178        i3     c30        0         2         A     571542116_01   
3       178        i3     c30        0         2         B  571542116_02.96   
4       178        i3     c30        0         3         A     571542116_01   
5       178        i3     c30        0         3         B  571542116_02.96   
6       178        i3     c30        0         4         A     571542116_01   
7       178        i3     c30        0         4         B  571542116_02.96   

        out_edge_id turn_type node_type  
0                         NaN     coord  
1                         NaN     coord  
2  -571542116_02.96         S     coord  
3  571542116_02.164         S     coord  
4  -571542116_02.96         S     coord  
5  571542116_02.164         S     coord  
6  -571542116_02.96         S     coord  
7  571542116_02.164         S     coord

In [24]:
self.matcher = pd.concat([self.angle, *uangles, self.coord])
self.matcher[:60]

inter_no  phase_no ring_type  STOS_NO node_id parent_id  inc_angle  \
0         175         1         A        0      i0        i0      179.0   
1         175         1         B        0      i0        i0        3.0   
2         175         2         A        0      i0        i0        1.0   
3         175         2         B        0      i0        i0      179.0   
4         175         3         A        0      i0        i0       92.0   
5         175         3         B        0      i0        i0       90.0   
6         175         4         A        0      i0        i0      268.0   
7         175         4         B        0      i0        i0      270.0   
16        176         1         A        0      i1        i1      180.0   
17        176         1         B        0      i1        i1      359.0   
18        176         2         A        0      i1        i1      180.0   
19        176         2         B        0      i1        i1      180.0   
20        176         3         A        0      i1        i1      270.0   
21        176         3         B        0      i1        i1        NaN   
32        177         1         A        0      i2        i2      180.0   
33        177         1         B        0      i2        i2        1.0   
34        177         2         A        0      i2        i2      180.0   
35        177         2         B        0      i2        i2        1.0   
36        177         3         A        0      i2        i2        NaN   
37        177         3         B        0      i2        i2        NaN   
38        177         4         A        0      i2        i2      180.0   
39        177         4         B        0      i2        i2        1.0   
48        178         1         A        0      i3        i3      180.0   
49        178         1         B        0      i3        i3        0.0   
50        178         2         A        0      i3        i3        0.0   
51        178         2         B        0      i3        i3      180.0   
52        178         3         A        0      i3        i3      270.0   
53        178         3         B        0      i3        i3      270.0   
54        178         4         A        0      i3        i3       90.0   
55        178         4         B        0      i3        i3       90.0   
64        201         1         A        0      i8        i8      180.0   
65        201         1         B        0      i8        i8      180.0   
66        201         2         A        0      i8        i8      270.0   
67        201         2         B        0      i8        i8      270.0   
68        201         3         A        0      i8        i8       90.0   
69        201         3         B        0      i8        i8      270.0   
70        201         4         A        0      i8        i8       90.0   
71        201         4         B        0      i8        i8       90.0   
72        201         5         A        0      i8        i8        0.0   
73        201         5         B        0      i8        i8        0.0   
80        202         1         A        0      i9        i9       90.0   
81        202         1         B        0      i9        i9      270.0   
82        202         2         A        0      i9        i9        NaN   
83        202         2         B        0      i9        i9        NaN   
96        206         1         A        0      i7        i7      180.0   
97        206         1         B        0      i7        i7        0.0   
98        206         2         A        0      i7        i7        NaN   
99        206         2         B        0      i7        i7        NaN   
100       206         3         A        0      i7        i7      180.0   
101       206         3         B        0      i7        i7        0.0   
102       206         4         A        0      i7        i7        NaN   
103       206         4         B        0      i7        i7        NaN   
112       210         1       